In [4]:
# created on Dec 24, 2020
# @author:          Bo Zhao
# @email:           zhaobo@uw.edu
# @website:         https://hgis.uw.edu
# @organization:    Department of Geography, University of Washington, Seattle
# @description:     Search geo-tagged tweets within the U.S. This script is modified from https://github.com/shawn-terryah/Twitter_Geolocation

!python -m pip install tweepy
import tweepy, json, time

DEPRECATION: Python 2.7 reached the end of its life on January 1st, 2020. Please upgrade your Python as Python 2.7 is no longer maintained. A future version of pip will drop support for Python 2.7. More details about Python 2 support in pip, can be found at https://pip.pypa.io/en/latest/development/release-process/#python-2-support
Defaulting to user installation because normal site-packages is not writeable


In [5]:
class StreamListener(tweepy.StreamListener):
    """
    tweepy.StreamListener is a class provided by tweepy used to access
    the Twitter Streaming API to collect tweets in real-time.
    """

    def __init__(self, time_limit=60, file=""):
        """class initialization"""
        self.start_time = time.time()
        self.limit = time_limit
        self.f = open(file, 'a', encoding="utf-8")
        super(StreamListener, self).__init__()

    def on_data(self, data):
        """This is called when data are streamed in."""
        if (time.time() - self.start_time) < self.limit:
            datajson = json.loads(data)
            print (datajson, "\n")
            id = datajson['id']
            username = datajson['user']['screen_name']
            created_at = datajson['created_at']
            text = datajson['text'].strip().replace("\n", "")

            # process the geo-tags
            if datajson['coordinates'] == None:
                bbox = datajson['place']['bounding_box']['coordinates'][0]
                lng = (bbox[0][0] + bbox[2][0]) / 2.0
                lat = (bbox[0][1] + bbox[1][1]) / 2.0
            else:
                lng = datajson['coordinates']['coordinates'][0]
                lat = datajson['coordinates']['coordinates'][1]

            record = '%d, %s, %s, %f, %f, %s \n' % (id, username, created_at, lng, lat, text)
            print (record)
            self.f.write(record)
        else:
            self.f.close()
            print ("finished")
            return False

In [6]:
if __name__ == "__main__":
    # These are provided to you through the Twitter API after you create a account
    # register a Twitter App to get the keys and access tokens.
    output_file = "assets/tweets.csv"

    # Apply for your own Twitter API keys at https://developer.twitter.com/en/apply-for-access
    consumer_key = "NRa1XcJ7z6jaGc022a6IQHJQo"
    consumer_secret = "0T5xOp5wywvI32feOcfGki8sxPtHApbhWjmMsp8r8NwV9BYjtf"
    access_token = "731035579-CPZKHLEChsnSq142gYUERm8rRJt3dYO9pOMKlY0t"
    access_token_secret = "me0PlLgVLpueAVazqU10C4CBIh45cecp5vgrJVPrd8XkC"

    myauth = tweepy.OAuthHandler(consumer_key, consumer_secret)
    myauth.set_access_token(access_token, access_token_secret)

    # LOCATIONS are the longitude, latitude coordinate corners for a box that restricts the
    # geographic area from which you will stream tweets. The first two define the southwest
    # corner of the box and the second two define the northeast corner of the box.
    LOCATIONS = [-124.7771694, 24.520833, -66.947028, 49.384472,  # Contiguous US
                 -164.639405, 58.806859, -144.152365, 71.76871,  # Alaska
                 -160.161542, 18.776344, -154.641396, 22.878623]  # Hawaii

    stream_listener = StreamListener(time_limit=90, file=output_file)
    stream = tweepy.Stream(auth=myauth, listener=stream_listener)
    stream.filter(locations=LOCATIONS)
    stream.filter(track=['scenery'])


{'created_at': 'Wed Apr 22 20:43:19 +0000 2020', 'id': 1253061847751811073, 'id_str': '1253061847751811073', 'text': 'Absolutely #SherlockHolmes style investigation!! Very thorough!', 'source': '<a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>', 'truncated': False, 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 2434898731, 'id_str': '2434898731', 'name': 'Brent Radford', 'screen_name': 'brentradford4', 'location': 'Montreal', 'url': None, 'description': 'Filmmaker, film tech, chief cook and bottle washer.', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 101, 'friends_count': 151, 'listed_count': 35, 'favourites_count': 302, 'statuses_count': 2062, 'created_at': 'Wed Apr 09 04:31:04 +0000 2014', 'utc_offset': None, 'time_zone': None, 'geo_enabled': True, 'lang': None, 'contributors_enabled

{'created_at': 'Wed Apr 22 20:43:20 +0000 2020', 'id': 1253061849056075776, 'id_str': '1253061849056075776', 'text': '@IrrationalHawk I would love that 💛🖤💛🖤', 'display_text_range': [16, 38], 'source': '<a href="http://twitter.com/download/android" rel="nofollow">Twitter for Android</a>', 'truncated': False, 'in_reply_to_status_id': 1253017698012930048, 'in_reply_to_status_id_str': '1253017698012930048', 'in_reply_to_user_id': 1300579416, 'in_reply_to_user_id_str': '1300579416', 'in_reply_to_screen_name': 'IrrationalHawk', 'user': {'id': 302943453, 'id_str': '302943453', 'name': 'Sherry Marek', 'screen_name': 'SherryMarek', 'location': 'Miami, FL', 'url': 'http://www.DatavisionTech.com', 'description': 'Co-founder Datavision Technologies, wife, mom of 3 awesome kids, 2 4-legged kids, healthy lifestyle, Iowa Hawkeyes fan.Tweets are my own :)', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 955, 'friends_count': 2596, 'listed_count': 131, 'favourites_

{'created_at': 'Wed Apr 22 20:43:20 +0000 2020', 'id': 1253061849966358531, 'id_str': '1253061849966358531', 'text': '@BeyondTheVeilI1 @OriginalGenSen @iSwampDweller @LadySpookaria @Staceybuzz2013 @stalking_78 @SlumberReads… https://t.co/ZBGscLxuCx', 'display_text_range': [117, 140], 'source': '<a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>', 'truncated': True, 'in_reply_to_status_id': 1252962025287880705, 'in_reply_to_status_id_str': '1252962025287880705', 'in_reply_to_user_id': 1170806620324077568, 'in_reply_to_user_id_str': '1170806620324077568', 'in_reply_to_screen_name': 'BeyondTheVeilI1', 'user': {'id': 1214676759775461376, 'id_str': '1214676759775461376', 'name': 'Tales from Oak Hill', 'screen_name': 'TalesOakHill', 'location': 'Lone Star State', 'url': 'https://www.youtube.com/TalesfromOakHill', 'description': 'Youtuber. Horror Narrator. Former opera singer. 50% Cowboy. 50% Priest. 100% Profanity Professional. Alter ego: @dustinmeyer', 'trans

{'created_at': 'Wed Apr 22 20:43:20 +0000 2020', 'id': 1253061850687852544, 'id_str': '1253061850687852544', 'text': '@M1lton2 It’s so slept on 😐', 'display_text_range': [9, 27], 'source': '<a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>', 'truncated': False, 'in_reply_to_status_id': 1253059935920951299, 'in_reply_to_status_id_str': '1253059935920951299', 'in_reply_to_user_id': 3299208337, 'in_reply_to_user_id_str': '3299208337', 'in_reply_to_screen_name': 'M1lton2', 'user': {'id': 38813938, 'id_str': '38813938', 'name': '𝔄𝔪𝔟𝔢𝔯¹³🔮♓', 'screen_name': 'AmberLMAguilera', 'location': 'Texas, USA', 'url': None, 'description': 'Modify your energy so your bank and your skin glow.\n♓💎🎶 Mila 💘. Lover. Poet. Emo. I fucking love Taylor Swift.', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 539, 'friends_count': 661, 'listed_count': 6, 'favourites_count': 47368, 'statuses_count': 85566, 'created_at': 'Sat May 09 06:50:18 +000

{'created_at': 'Wed Apr 22 20:43:20 +0000 2020', 'id': 1253061851866443785, 'id_str': '1253061851866443785', 'text': '@DPSwanson26 @akashicenergy @Shill_DS @ComandanteMoose @JNJNews Ugh. Standard BS challenge - do your own research o… https://t.co/VNq0VYQj9u', 'display_text_range': [64, 140], 'source': '<a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>', 'truncated': True, 'in_reply_to_status_id': 1253048691016912896, 'in_reply_to_status_id_str': '1253048691016912896', 'in_reply_to_user_id': 550287986, 'in_reply_to_user_id_str': '550287986', 'in_reply_to_screen_name': 'DPSwanson26', 'user': {'id': 745294344748417024, 'id_str': '745294344748417024', 'name': 'deirdre mullen', 'screen_name': 'Mullen65Mullen', 'location': None, 'url': None, 'description': None, 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 45, 'friends_count': 209, 'listed_count': 0, 'favourites_count': 1851, 'statuses_count': 694, 'created_at': 'Tue J

...

{'created_at': 'Wed Apr 22 20:44:48 +0000 2020', 'id': 1253062219547451392, 'id_str': '1253062219547451392', 'text': '@WonpiI_Day6 HOLLON MAYA YOU MAY HAVE PUT ME ON SOMETHING', 'display_text_range': [13, 57], 'source': '<a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>', 'truncated': False, 'in_reply_to_status_id': 1253059825694539776, 'in_reply_to_status_id_str': '1253059825694539776', 'in_reply_to_user_id': 289021312, 'in_reply_to_user_id_str': '289021312', 'in_reply_to_screen_name': 'WonpiI_Day6', 'user': {'id': 913648745450938368, 'id_str': '913648745450938368', 'name': 'dowoons tiddie', 'screen_name': 'dae6hwi', 'location': 'ab6ix day6 the rose jsw kjh', 'url': None, 'description': '## DAEHWI: I thought I left you in 2018', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 110, 'friends_count': 86, 'listed_count': 9, 'favourites_count': 3321, 'statuses_count': 2857, 'created_at': 'Fri Sep 29 06:16:50 +0000 2017',

{'created_at': 'Wed Apr 22 20:44:48 +0000 2020', 'id': 1253062220541358081, 'id_str': '1253062220541358081', 'text': 'Love/hate relationship with being sore. \n\nLove knowing my muscles are getting shape. 😘👌🏼\n\nHate knowing my fat ass n… https://t.co/T5Ie5evFqr', 'source': '<a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>', 'truncated': True, 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 1681163642, 'id_str': '1681163642', 'name': 'Bri Modesto 🌷', 'screen_name': 'BrittanyModesto', 'location': None, 'url': None, 'description': None, 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 303, 'friends_count': 560, 'listed_count': 0, 'favourites_count': 12315, 'statuses_count': 6567, 'created_at': 'Sun Aug 18 16:55:15 +0000 2013', 'utc_offset': None, 'time_zone': None, 'geo_enabled': True, 'lang':

{'created_at': 'Wed Apr 22 20:44:49 +0000 2020', 'id': 1253062221812256768, 'id_str': '1253062221812256768', 'text': '@vazquezz__ That’s what drugs do to ya kids', 'display_text_range': [12, 43], 'source': '<a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>', 'truncated': False, 'in_reply_to_status_id': 1253060166683103233, 'in_reply_to_status_id_str': '1253060166683103233', 'in_reply_to_user_id': 735108104543555585, 'in_reply_to_user_id_str': '735108104543555585', 'in_reply_to_screen_name': 'vazquezz__', 'user': {'id': 1219274602989465600, 'id_str': '1219274602989465600', 'name': 'Anaida Naya Vazquez', 'screen_name': 'AnaidaNaya', 'location': 'Houston, TX', 'url': None, 'description': '🇨🇱🤘🏽🌇 •♍️96🎉 •👩\u200d👦Cisco •🦸🏻\u200d♂️👨🏽\u200d🏭I.C.💖 IG:@naya_vazquez SC:anaida_96👻 FB:NayaVazquez', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 378, 'friends_count': 499, 'listed_count': 0, 'favourites_count': 4466, 'statuses_cou

{'created_at': 'Wed Apr 22 20:44:49 +0000 2020', 'id': 1253062223326576640, 'id_str': '1253062223326576640', 'text': '4:44', 'source': '<a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>', 'truncated': False, 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 22436309, 'id_str': '22436309', 'name': 'The Man Behind The Camera', 'screen_name': 'LilCoachTMBTC', 'location': None, 'url': None, 'description': 'Documentarian | Creative | Visual Architect | Published | Instagram: lilcoachtmbtc', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 7371, 'friends_count': 439, 'listed_count': 67, 'favourites_count': 690, 'statuses_count': 153610, 'created_at': 'Mon Mar 02 01:55:28 +0000 2009', 'utc_offset': None, 'time_zone': None, 'geo_enabled': True, 'lang': None, 'contributors_enabled': False, 'is_translato

finished
finished
